In [1]:
import pandas as pd
import numpy as np
import cv2
test_images_folder_path = "/Users/sschickler/ML_DATA/Clouds/test_images"
train_images_folder_path = "/Users/sschickler/ML_DATA/Clouds/train_images"
train_labels_path = "/Users/sschickler/ML_DATA/train.csv"
pickle_file_path = "/Users/sschickler/ML_DATA/train_labels.pickle"
 


Creates list of all the train image file names

In [2]:
import os
train_images_file_names = list(os.walk(train_images_folder_path))[0][2]
train_images_file_paths = [os.path.join(train_images_folder_path, x) for x in train_images_file_names]
print(train_images_file_paths)

['/Users/sschickler/ML_DATA/Clouds/train_images/8734e73.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/0ece863.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/c54d2ef.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/3124a1e.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/a438b48.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/94aff90.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/eb8ac47.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/e298926.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/4c60d33.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/d84a0d8.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/6158df3.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/d5a17de.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/60bac00.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/59f6a74.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/77d4125.jpg', '/Users/sschickler/ML_DATA/Clouds/train_images/74e1590.jpg', '/Users/sschickler/ML_D

In [3]:
test_image = cv2.imread(train_images_file_paths[0])
image_shape = test_image.shape
print(image_shape)

(1400, 2100, 3)


Loads label CSV

In [4]:
#I didn't write this block copied it from here: https://www.kaggle.com/robertkag/rle-to-mask-converter 
#The image pixels are encoded in a run length encoder which is hard-ish to decode

def rleToMask(rleString,height,width):
  rows,cols = height,width
  rleNumbers = np.array(rleString.split(' '), dtype=int)
  rlePairs = rleNumbers.reshape(-1,2)
  print(rlePairs)
  img = np.zeros(rows*cols,dtype=np.byte)
  for index,length in rlePairs:
    index -= 1
    img[index:index+length] = 255
  img = img.reshape(cols,rows)
  img = img.T
  
  return img

In [5]:
import pickle
def find2DCordinates(cord_1D, image_height, image_width):
    return int(cord_1D/image_width),cord_1D%image_width

      
      
  print(rlePairs)
# a list of each image with image_name and then another list with each encoding
label_list = []
def readTrainData(path_train, pickle_path):
    if os.path.isfile(pickle_path) and False:
        print("Pickle File Exists, loading file")
        with open(pickle_path, 'rb') as pickle_file:
            return pickle.load(pickle_file)
    print("Pickle File doesn't Exists, processsing data")
    labels = pd.read_csv(path_train)
    labels.head(10) #prints out first 10 rows of labels
    labels.fillna(-1, inplace=True)
    for image_iter in range(0,len(labels),4):
        label_list.append({"image_name": labels["Image_Label"][image_iter].split("_")[0], 
                           "Encodings":
                               [{"Label": labels["Image_Label"][image_iter+label_iter].split("_")[1],
                                 "EncodedPixels": rleToMask(labels["EncodedPixels"][image_iter+label_iter],
                                                            image_shape[0],image_shape[1]) if labels["EncodedPixels"][image_iter+label_iter] != -1 else np.array([])} 
                                         for label_iter in range(4)]})
    
    with open(pickle_path, "wb") as pickle_file:
        pickle.dump(label_list, pickle_file)
    return label_list

labels_processed = readTrainData(train_labels_path, pickle_file_path)

Pickle File doesn't Exists, processsing data
[[ 264918     937]
 [ 266318     937]
 [ 267718     937]
 ...
 [1653718     937]
 [1655118     937]
 [1656518     937]]
[[1355565    1002]
 [1356965    1002]
 [1358365    1002]
 ...
 [2929196     644]
 [2930596     644]
 [2931996     644]]
[[ 233813     878]
 [ 235213     878]
 [ 236613     878]
 ...
 [2920638       6]
 [2920647       2]
 [2920650     641]]
[[1339279     519]
 [1340679     519]
 [1342079     519]
 ...
 [2933879     519]
 [2935279     519]
 [2936679     519]]
[[  67495     350]
 [  68895     350]
 [  70295     350]
 ...
 [1319095     350]
 [1320495     350]
 [1321895     350]]
[[   3510     690]
 [   4910     690]
 [   6310     690]
 ...
 [2547639       1]
 [2547641       2]
 [2547644     356]]
[[   2047     703]
 [   3447     703]
 [   4847     703]
 ...
 [2076847     703]
 [2078247     703]
 [2079647     703]]
[[ 658170     388]
 [ 659570     388]
 [ 660970     388]
 ...
 [1761370     388]
 [1762770     388]
 [1764170     3

In [ ]:
test = labels_processed[0]["Encodings"][0]["EncodedPixels"]
np.unique(test)

In [ ]:
#Not done yet but it should take an rle image mask and convert it to a box with 4 corners
def rleToBox(rleString,height,width): #turn the RLE encoded string into an array of bounding boxes
  rows,cols = height,width
  rleNumbers = np.array(rleString.split(' '), dtype=int)
  rlePairs = rleNumbers.reshape(-1,2)
  while len(rlePairs)!= 0:
      corners = [(0,0) for _ in range(4)]
      corners[0] = find2DCordinates(rlePairs[0][0], height, width)
      corners[1] = find2DCordinates(rlePairs[0][0]+rlePairs[0][1], height, width)
      box_height = len(np.where(rlePairs[:,1]==rlePairs[0][1]))
      final_item = rlePairs[box_height-1]
      print(final_item)

In [ ]:
#Displays an image mask from an RLE 
def displayImageMaskRLE(rleString, height, width):  # displays image from RLE
    rows, cols = height, width
    rleNumbers = np.array(rleString.split(' '), dtype=int)
    rlePairs = rleNumbers.reshape(-1, 2)
    print(rlePairs)
    img = np.zeros(rows * cols, dtype=np.byte)
    for index, length in rlePairs:
        index -= 1
        img[index:index + length] = 255
    img = img.reshape(cols, rows)
    img = img.T
    plt.imshow(img, cmap='gray')
    plt.show()